# Combine CTD data
- take daily profiles saved as pickle files that are ooipy.basic.CTD.profile objects and convert them into a single netCDF file.

In [7]:
import ooipy
import pickle
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import os
from tqdm import tqdm

plt.rcParams['font.family'] = 'serif'
plt.rcParams['font.size'] = 14
plt.rcParams['text.usetex']=True

import hvplot.xarray
import holoviews as hv

import seaborn as sns

In [4]:
sns.set_palette('rocket')

### Load profiles into memory

In [2]:
file_base = '/Volumes/Ocean_Acoustics/CTD_Data_ooipy/only_profilers/axial_base/'
files = os.listdir(file_base)
files.sort()
_ = files.pop(0)

In [3]:
profiles = []
for file in tqdm(files):
    with open(file_base+file, 'rb') as f:
        profiles.append(pickle.load(f))            

100%|██████████████████████████████████████| 3029/3029 [00:21<00:00, 141.75it/s]


### Convert to netCDF

In [5]:
def build_ssp(profiles, files):
    '''
    
    Parameters
    ----------
    profiles : list
        list of profiles
    files : list
        list of file names (should be dates)
    '''
    ssps = []
    for k, profile in enumerate(profiles):
        if np.isnan(profile.depth_mean[0]):
            first_depth_idx = 0
        else:
            first_depth_idx = int(np.floor(profile.depth_mean[0]))

        profile_gridded = np.hstack((np.ones(first_depth_idx)*np.nan, profile.parameter_mean))[:3000]

        ssps.append(profile_gridded)
    ssps = np.array(ssps)
    
    # build time coord
    time_coord = []
    for file in files:
        time_coord.append(pd.Timestamp(file[:-4]))
        
    sspx = xr.DataArray(ssps, dims=['time', 'depth'], coords={'time':time_coord, 'depth':np.arange(3000)}, name='CTD SSP (only profilers)')
    
    return sspx

In [6]:
sspx = build_ssp(profiles, files)
sspx.loc[:,10:1500].hvplot(x='time', y='depth', rasterize=True, width=1000, title='CTD data from shallow / deep profiles - Axial Base')

:DynamicMap   []
   :Image   [time,depth]   (CTD SSP (only profilers))

In [9]:
fn = '/Volumes/Ocean_Acoustics/CTD_Data_ooipy/only_profilers/axial_base_onlyprofilers.nc'
sspx.to_netcdf(fn)

### create deep profile mean
- hand tune and remove outliers

In [52]:
sspx = build_ssp(profiles, files)

ssp_slice = sspx.loc[pd.Timestamp('2018-08-01'):pd.Timestamp('2023-01-18')]

# hand remove outliers
ssp_slice.loc[pd.Timestamp('2019-09-13'),180:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-07-28'),:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-07-29'),:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-07-03'):pd.Timestamp('2019-07-04'),188:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-07-16'),1545:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-03-25'),:] = np.nan
ssp_slice.loc[pd.Timestamp('2019-06-16'):pd.Timestamp('2019-07-01'),184:] = np.nan
ssp_slice.loc[pd.Timestamp('2020-09-29'):pd.Timestamp('2020-10-19'),187:] = np.nan
ssp_slice.loc[pd.Timestamp('2021-08-15'):pd.Timestamp('2022-01-01'),187:] = np.nan
after_clean = ssp_slice.loc[:,187:1550].hvplot.image(x='time', rasterize=True)

In [51]:
after_clean.opts(width=500, height=200)

:DynamicMap   []
   :Image   [time,depth]   (CTD SSP (only profilers))

In [58]:
deep_mean = ssp_slice.loc[:,:1550].mean('time')
deep_std = ssp_slice.loc[:,:1550].std('time')

In [121]:
fig1 = plt.figure(figsize=(3,6))
plt.plot(deep_mean.values, deep_mean.depth, c='C0')

plt.plot(deep_mean-deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)
plt.plot(deep_mean+deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)

plt.fill_betweenx(deep_mean.depth, deep_mean-deep_std/2, deep_mean + deep_std/2, alpha=1, color='C5')
plt.grid()
plt.ylim([1550,0])
plt.xlabel('sound speed [m/s]')
plt.ylabel('depth [m]')
plt.tight_layout()
plt.close()

fig2 = plt.figure(figsize=(3,3))
plt.plot(deep_mean.values, deep_mean.depth)
plt.plot(deep_mean-deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)
plt.plot(deep_mean+deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)

plt.fill_betweenx(deep_mean.depth, deep_mean-deep_std/2, deep_mean + deep_std/2, color='C5')
plt.grid()
plt.ylim([800,200])
plt.xlim([1475, 1480])
plt.xlabel('sound speed [m/s]')
plt.ylabel('depth [m]')
plt.tight_layout()
plt.close()

fig3 = plt.figure(figsize=(3,3))
plt.plot(deep_mean.values, deep_mean.depth)
plt.plot(deep_mean-deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)
plt.plot(deep_mean+deep_std/2, deep_mean.depth, linewidth=0.5, c='k', alpha=0.5)

plt.fill_betweenx(deep_mean.depth, deep_mean-deep_std/2, deep_mean + deep_std/2, color='C5')
plt.grid()
plt.ylim([200,0])
#plt.xlim([1475, 1480])
plt.xlabel('sound speed [m/s]')
plt.ylabel('depth [m]')
plt.tight_layout()
plt.close()

fig1.savefig('sound_speed_std.svg')
fig2.savefig('sound_speed_std_zoom1.svg')
fig3.savefig('sound_speed_std_zoom2.svg')

In [130]:
fn = '/Volumes/Ocean_Acoustics/CTD_Data_ooipy/only_profilers/deep_profile_mean.nc'
deep_mean.loc[180:].to_netcdf(fn)

fn = '/Volumes/Ocean_Acoustics/CTD_Data_ooipy/only_profilers/deep_profile_std.nc'
deep_std.loc[180:].to_netcdf(fn)